In [1]:
!pip uninstall gym-jsbsim -y
!pip install jsbsim
!pip uninstall gym-jsbsim -y
!python3 setup.py install
!pip install -e ./

Found existing installation: gym-jsbsim 0.6.7
Uninstalling gym-jsbsim-0.6.7:
  Successfully uninstalled gym-jsbsim-0.6.7
jsbsim-1.1.11/aircraft/
jsbsim-1.1.11/aircraft/737/
jsbsim-1.1.11/aircraft/737/737.xml
jsbsim-1.1.11/aircraft/737/INSTALL
jsbsim-1.1.11/aircraft/737/cruise_init.xml
jsbsim-1.1.11/aircraft/737/cruise_steady_turn_init.xml
jsbsim-1.1.11/aircraft/737/reset00.xml
jsbsim-1.1.11/aircraft/A320/
jsbsim-1.1.11/aircraft/A320/A320.xml
jsbsim-1.1.11/aircraft/A320/INSTALL
jsbsim-1.1.11/aircraft/A4/
jsbsim-1.1.11/aircraft/A4/A4.xml
jsbsim-1.1.11/aircraft/A4/INSTALL
jsbsim-1.1.11/aircraft/B17/
jsbsim-1.1.11/aircraft/B17/B17.xml
jsbsim-1.1.11/aircraft/B17/INSTALL
jsbsim-1.1.11/aircraft/B17/reset00.xml
jsbsim-1.1.11/aircraft/B747/
jsbsim-1.1.11/aircraft/B747/B747.xml
jsbsim-1.1.11/aircraft/B747/INSTALL
jsbsim-1.1.11/aircraft/B747/reset00.xml
jsbsim-1.1.11/aircraft/Boeing314/
jsbsim-1.1.11/aircraft/Boeing314/Boeing314.xml
jsbsim-1.1.11/aircraft/Boeing314/INSTALL
jsbsim-1.1.11/aircraft/

In [2]:
import gym
import gym_jsbsim
from gym_jsbsim.catalogs.catalog import Catalog as c
import numpy as np
import math
import random
import torch
from torch import nn
import torch.nn.functional as F

In [18]:
class PolicyNetwork(nn.Module):
    def __init__(self,num_hidden_neurons):
        super(PolicyNetwork, self).__init__()
        self.layer1 = nn.Linear(11,num_hidden_neurons)
        self.layer2 = nn.Linear(num_hidden_neurons,4)

    def forward(self, x):
        x=torch.tanh(self.layer1(x))
        x=torch.tanh(self.layer2(x))
        return x

In [19]:
np.random.seed(0)
random.seed(0)
# init_models = []
# for i in range(5000):
#   torch.manual_seed(i)
#   model = PolicyNetwork(16)
#   for param in model.parameters():
#       param.requires_grad = False
#   init_models.append(model)
#init_center = np.concatenate((model.layer1.weight.data.numpy().flatten(),model.layer2.weight.data.numpy().flatten()))
torch.manual_seed(1453)
model = PolicyNetwork(16)
for param in model.parameters():
  param.requires_grad = False
init_center = np.concatenate((model.layer1.weight.data.numpy().flatten(),model.layer2.weight.data.numpy().flatten()))

In [21]:
def vec_to_weights(vec,num_hidden_neurons):
  w1 = torch.from_numpy(np.reshape(vec[0:num_hidden_neurons*11], (num_hidden_neurons, 11))).float()
  w2 = torch.from_numpy(np.reshape(vec[num_hidden_neurons*11:15*num_hidden_neurons], (4, num_hidden_neurons))).float()
  return w1,w2

In [22]:
class Obs_TupleToBoxWrapper(gym.ObservationWrapper):
    def __init__(self, env):
        super().__init__(env)
        low = np.empty(shape=(0,))
        high = np.empty(shape=(0,))
        for i in env.observation_space:
          low = np.concatenate([low,i.low])
          high = np.concatenate([high,i.high])
        self.observation_space = gym.spaces.Box(low=low, high=high, dtype="float")
        
    
    def observation(self, obs):
        new_obs = np.empty(shape=(0,))
        for i in obs:
          new_obs = np.concatenate([new_obs,i])
        return new_obs

In [23]:
class Act_TupleToBoxWrapper(gym.ActionWrapper):
    def __init__(self, env):
        super().__init__(env)
        low = np.empty(shape=(0,))
        high = np.empty(shape=(0,))
        for i in env.action_space:
          low = np.concatenate([low,i.low])
          high = np.concatenate([high,i.high])
        self.action_space = gym.spaces.Box(low=low, high=high, dtype="float")
        
    
    def action(self, act):
#        print(act)
#        new_act = np.empty(shape=(0,))
#        for i in act:
#          new_act = np.concatenate([new_act,i])
        return act

In [24]:
env=Act_TupleToBoxWrapper(Obs_TupleToBoxWrapper(gym.make("GymJsbsim-HeadingControlTask-v0")))

/home/andrew/.local/lib/python3.8/site-packages/gym/spaces/box.py:73: UserWarning: WARN: Box bound precision lowered by casting to float64
  logger.warn(


In [25]:
def find_and_take_action(env,curr_state,nn):
  action = nn(torch.from_numpy(curr_state).float())
  action.numpy()
  action[-1]=(action[-1]+1)*0.45
  state, reward, done, _ = env.step(action)
  return state, reward, done

In [33]:
def run_episode(env,nn,find_and_take_action):
  episode_reward = 0
  state = env.reset()
  #print("Initial State =", state)
  done = False
  while not done:
    state, reward, done = find_and_take_action(env,state,nn)
    episode_reward += reward
    #print("action =", action, " ---> State =", state, " : Reward =", reward)
  #print("Simulation Time = "+"{:.3f}".format(env.get_sim_time())+" sec")
  #print("Episode Reward = "+"{:.3f}".format(episode_reward))
  if(env.get_sim_time()<150):
    objective = env.get_sim_time()-150
  elif(env.get_sim_time()>150.0000000000115):
    objective = episode_reward
  else:
    objective = (1/abs(state[0]+1))*(1/abs(state[1]+1))
  return env.get_sim_time(),episode_reward,objective

In [ ]:
# init_center_rewards = []
# init_center_times = []
# for i in range(5000):
#   init_center_reward, init_center_time = run_episode(env,init_models[i],find_and_take_action)
#   init_center_rewards.append(init_center_reward)
#   init_center_times.append(init_center_time)
# init_center_reward = max(init_center_rewards)
# id = init_center_rewards.index(init_center_reward)
# init_center_time = init_center_times[id]
# init_center = np.concatenate((init_models[id].layer1.weight.data.numpy().flatten(),init_models[id].layer2.weight.data.numpy().flatten()))

In [34]:
init_center_time, init_center_reward, init_center_objective = run_episode(env,model,find_and_take_action)


In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 251
Engine location ignored, only thruster location is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 256
Engine orientation ignored, only thruster orientation is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 276
Engine location ignored, only thruster location is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 281
Engine orientation ignored, only thruster orientation is used.


In [36]:
#muller-marsaglia method
def spherepicking(n):
    while True:           #to get rid off [0,0,0,0] case
        l = [random.gauss(0, 1) for i in range(n)]
        sumsq = sum([x * x for x in l])
        if sumsq > 0:
            break
    norm = 1.0 / math.sqrt(sumsq)
    pt = [x * norm for x in l]
    return np.array(pt)

In [38]:
def hill_climbing(env,spherepicking,lr,init_center,init_center_reward,init_center_time,init_center_objective,num_hidden_neurons,num_points,run_episode,find_and_take_action):

  models = []
  init_w1, init_w2 = vec_to_weights(init_center,num_hidden_neurons)
  for i in range(num_points):
    models.append(PolicyNetwork(num_hidden_neurons))
    for param in models[i].parameters():
      param.requires_grad = False

  center_is_best = False
  num_weights = num_hidden_neurons*11 + 4*num_hidden_neurons
  center = init_center
  reward = init_center_reward
  time = init_center_time
  objective = init_center_objective
  step = 0
  print("Step = ",step)
  print("Simulation Time = ",time," sec")
  print("Reward = ",reward)
  print("Objective = ",objective)

  while not center_is_best:
    rewards = []
    sim_time = []
    objectives = []
    points = []
    for i in range(num_points):
      point = center + lr*spherepicking(num_weights)
      points.append(point)
      w1, w2 = vec_to_weights(point,num_hidden_neurons)
      models[i].layer1.weight.data = w1
      models[i].layer2.weight.data = w2
      t, r, o = run_episode(env,models[i],find_and_take_action)
      rewards.append(r)
      sim_time.append(t)
      objectives.append(o)
    max_objective = max(objectives)
    id = objectives.index(max_objective)
    if(max_objective<objective):
      center_is_best = True
      best_vec = center
    else:
      objective = max_objective
      time = sim_time[id]
      reward = rewards[id]
      step+=1
      print("Step = ",step)
      print("Simulation Time = ",time," sec")
      print("Reward = ",reward)
      print("Objective = ",objective)
      center = points[id]
      new_w1, new_w2 = vec_to_weights(center,num_hidden_neurons)
      for i in range(num_points):
        models[i].layer1.weight.data = new_w1
        models[i].layer2.weight.data = new_w2
  return best_vec    

In [39]:
best_weights = hill_climbing(env,spherepicking,1,init_center,init_center_reward,init_center_time,init_center_objective,16,10000,run_episode,find_and_take_action)

Step =  0
Simulation Time =  20.583333333333446  sec
Reward =  -37708060.46928328
Objective =  -129.41666666666654



In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 251
Engine location ignored, only thruster location is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 256
Engine orientation ignored, only thruster orientation is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 276
Engine location ignored, only thruster location is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 281
Engine orientation ignored, only thruster orientation is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 251
Engine location ignored, only thruster location is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 256
Engine 

Step =  1
Simulation Time =  150.0000000000115  sec
Reward =  -119113189.63126127
Objective =  27.252100843990092



In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 251
Engine location ignored, only thruster location is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 256
Engine orientation ignored, only thruster orientation is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 276
Engine location ignored, only thruster location is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 281
Engine orientation ignored, only thruster orientation is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 251
Engine location ignored, only thruster location is used.

In file /home/andrew/sem8/cs748/L2F_Challenge_YashGadhia/gym_jsbsim/jsbsim-1.1.11/aircraft/A320/A320.xml: line 256
Engine 

KeyboardInterrupt: 